# Madrid Restaurants Map Project

This project is generated as a coding challenge for a Data Engineer position at Carto. The main idea is get all the restaurants in Madrid that are 150 meters or more from the most closest cinema. It's developed using Python3. 

## Setup

This project utilizes the BigQuery API from Google to query the dataset. To get started, you'll need to provide your Google Cloud Credentials. Follow the steps outlined [here](https://developers.google.com/workspace/guides/create-credentials#service-account) to obtain the credentials file. Once you have the file, place it in the `./config/credentials.json` directory of this project.

### Running with Docker

We recommend running this notebook using Docker for consistency and ease of setup. Simply include your `credentials.json` file in the `config` folder, and Docker will automatically use it. If you haven't already, make sure Docker is installed on your system. You can find installation instructions [here](https://docs.docker.com/get-docker/).

### Running Locally

If you prefer to run the notebook locally, you'll need to set the credentials as an environment variable. Run the following code block to set the environment variable. Note that this step is only necessary for local execution.


In [1]:
# Uncomment the following line if you are running the script on a local machine
#import os
#os.environ["GOOGLE_APPLICATION_CREDENTIALS"] = "./config/credentials.json"

## Understanding the dataset

For this project, we're using a public dataset containing points of interest (POIs) from Spain. These POIs are sourced from Open Street Map (OSM) and stored in a table within BigQuery. Before we dive into the exercise, it's important to understand the structure of this dataset.

To do so, we'll retrieve the table schema using the following code block:

In [1]:
from google.cloud import bigquery


client = bigquery.Client()

table = client.get_table('carto-ps-bq-developers.data_test.osm_spain_pois')

table.schema

[SchemaField('id', 'INTEGER', 'NULLABLE', None, None, (), None),
 SchemaField('lon', 'FLOAT', 'NULLABLE', None, None, (), None),
 SchemaField('lat', 'FLOAT', 'NULLABLE', None, None, (), None),
 SchemaField('amenity', 'STRING', 'NULLABLE', None, None, (), None),
 SchemaField('shop', 'STRING', 'NULLABLE', None, None, (), None),
 SchemaField('leisure', 'STRING', 'NULLABLE', None, None, (), None),
 SchemaField('sport', 'STRING', 'NULLABLE', None, None, (), None),
 SchemaField('building', 'STRING', 'NULLABLE', None, None, (), None),
 SchemaField('entrance', 'STRING', 'NULLABLE', None, None, (), None),
 SchemaField('crossing', 'STRING', 'NULLABLE', None, None, (), None),
 SchemaField('the_geom', 'GEOGRAPHY', 'NULLABLE', None, None, (), None)]

## Filtering the Dataset

First, we need to filter the points of interest (POIs) based on their coordinates to include only those within the Metropolitan Area of Madrid. While the challenge provides four coordinates to define a "square" representing the Metropolitan Area, in a real-life scenario, we might use a polygon to accurately capture the area's shape.

Second, we further filter the POIs based on their type, specifically targeting restaurants and cinemas. We achieve this by examining the `amenity` column in the dataset. While there are various values in the `amenity` column, such as `fast_food`, indicating potential options for a delivery app, we opt to focus solely on POIs labeled strictly as `restaurant` because in this challenge we are focusing only in restaurants, not considering fast food, bars or any other kind of POIs.

This dual filtering approach ensures that we narrow down the dataset to include only relevant POIs within the Metropolitan Area of Madrid and of the specific type required for our analysis.

## Data Retrieval

Now that we have our configuration set up and understand the dataset, we can proceed with the data retrieval process. The `geo_analytics` module offers extensive customization options, allowing us to tailor the data retrieval process to our specific needs. In this scenario, we'll leverage the module to fulfill the requirements of the challenge.

To begin, we define constants for the longitude and latitude coordinates of Madrid. These constants represent the boundaries of the Metropolitan Area of Madrid and are used to filter all restaurants and cinemas located within Madrid.

In [2]:
from geo_analytics import query_geo_data_by_amenity

# We define constant lon and lat for Madrid city given by the following coordinates
LON = [-3.93455628, -3.31993445]
LAT = [40.25387182, 40.57085727]

restaurants = query_geo_data_by_amenity(LON, LAT, 'restaurant')
cinemas = query_geo_data_by_amenity(LON, LAT, 'cinema')

len(restaurants), len(cinemas)

Downloading: 100%|██████████|
Downloading: 100%|██████████|


(4531, 48)

### Filtering Restaurants by Proximity to Cinemas

Now that we have obtained all restaurants and cinemas within Madrid from the dataset, our next step is to filter the restaurants based on their proximity to cinemas. Specifically, we want to identify restaurants where the nearest cinema is at least 150 meters away.

To accomplish this task, we utilize the `filter_poi_proximity_to_group` function. This custom function takes two dataframes as input and filters the first dataframe based on its proximity to the second group. Additionally, the function accepts a distance parameter, which determines the proximity threshold for filtering.

In [3]:
from geo_analytics import filter_poi_by_proximity_to_group

MIN_DISTANCE_FROM_CINEMA = 150 # meters

restaurants_far_from_cinemas = filter_poi_by_proximity_to_group(restaurants, cinemas, MIN_DISTANCE_FROM_CINEMA)

restaurants_far_from_cinemas.head(), len(restaurants_far_from_cinemas)

(       poi_id        lat       lon                       geometry  \
 0  3903740912  40.423682 -3.686247  POINT (-3.6862466 40.4236817)   
 1  4942808513  40.430437 -3.692442  POINT (-3.6924422 40.4304375)   
 2  4966765724  40.438178 -3.794083  POINT (-3.7940831 40.4381777)   
 3  4349458099  40.413677 -3.708830   POINT (-3.7088298 40.413677)   
 4  6042650475  40.421296 -3.702904   POINT (-3.7029037 40.421296)   
 
                      nearest_poi  distance_to_nearest_poi  
 0  POINT (-3.6911335 40.4199239)               588.321699  
 1  POINT (-3.7008998 40.4301024)               718.637623  
 2  POINT (-3.7974782 40.4194401)              2100.528134  
 3  POINT (-3.7057283 40.4119892)               323.147746  
 4  POINT (-3.7058271 40.4204713)               264.462519  ,
 4165)

## Data Processing: Clustering Restaurants into Delivery Zones

Now that we have filtered all restaurants within Madrid that are at least 150 meters away from the nearest cinema, our next objective is to divide these restaurants into five distinct delivery zones based on their location. To achieve this, we employ the k-means clustering method.

### K-Means Clustering Overview

K-means clustering is a popular way to group data into clusters. It assigns each data point to the nearest cluster center and updates the centers based on the average of the points in each cluster. This repeats until the clusters stabilize, giving us groups where each point is closest to its cluster center.

### Application to Delivery Zone Formation

In our context, we leverage k-means clustering to divide Madrid into five distinct delivery zones. Each zone represents a cluster of restaurants that are geographically close to each other and can be served efficiently from a central point within the zone. By organizing restaurants into delivery zones, we can optimize delivery operations and ensure timely and efficient service to customers.


In [12]:
from geo_analytics import split_pois_by_clusters

restaurants_with_clusters = split_pois_by_clusters(restaurants_far_from_cinemas, 5)

restaurants_with_clusters.head()

/Users/mafer/Downloads/carto-challenge/geo_analytics/processing.py:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['cluster_id'] = kmeans.labels_


poi_id        lat       lon                       geometry  \
0  3903740912  40.423682 -3.686247  POINT (-3.6862466 40.4236817)   
1  4942808513  40.430437 -3.692442  POINT (-3.6924422 40.4304375)   
2  4966765724  40.438178 -3.794083  POINT (-3.7940831 40.4381777)   
3  4349458099  40.413677 -3.708830   POINT (-3.7088298 40.413677)   
4  6042650475  40.421296 -3.702904   POINT (-3.7029037 40.421296)   

                     nearest_poi  distance_to_nearest_poi  cluster_id  
0  POINT (-3.6911335 40.4199239)               588.321699           0  
1  POINT (-3.7008998 40.4301024)               718.637623           0  
2  POINT (-3.7974782 40.4194401)              2100.528134           2  
3  POINT (-3.7057283 40.4119892)               323.147746           0  
4  POINT (-3.7058271 40.4204713)               264.462519           0

## Exporting

Finally, we have a dataframe with the data we need for this exercise. But, we want to save this into a .csv file.

In [5]:
from geo_analytics import generate_map_csv

generate_map_csv(restaurants_with_clusters, './data/madrid_restaurants_clusters.csv')

## Visualization

Finally, we have our .csv generate with the restaurants within Madrid that are 150 meters or more away from the most nearest cinema. Now, we can use this file to make some analyze. 

In order to see how is the cluster distributed, we want to see all the restaurants in a Madrid's map, using different colors for each cluster. 

I decide to use folium to render this map, I also considered other options like [ipyleaflet](https://ipyleaflet.readthedocs.io/en/latest/). I ended up with folium because I founded it more simple for the initial configuration, and considering we want to render a simple map (just with different points) I think is enough for this exercise.

In [6]:
import pandas as pd
import folium

# We use the .csv file by default, but here we can use directly the DataFrame
# But using the .csv we allow user to only run the map generation code if they already have the .csv file
clustered_pois = pd.read_csv('./data/madrid_restaurants_clusters.csv')

# Define a color palette for different cluster IDs
cluster_colors = {
    0: 'blue',
    1: 'red',
    2: 'green',
    3: 'black',
    4: 'purple'
}

# We use a map centered in Madrid with a zoom level to see all the POIs
madrid_map = folium.Map(location=[40.4168, -3.7038], zoom_start=11)

for index, row in clustered_pois.iterrows():
    cluster_id = row['cluster_id']
    color = cluster_colors.get(cluster_id, 'gray') 
    folium.CircleMarker(
        location=[row['lat'], row['lon']],
        radius=4,
        color=color,
        fill=True,
        fill_color=color
    ).add_to(madrid_map)

madrid_map


For this initial map, as expected, we notice the highest density of restaurants in the center of Madrid. This aligns with expectations, as this area typically has the highest population density and a wide variety of commercial establishments. On otherside, we observe clusters such as the green one, which contain numerous outliers (restaurants located far from the center of Madrid), resulting in a significant expansion of this cluster.

Next, we will analyze the number of restaurants in each cluster and calculate the average distance from each restaurant in the cluster to the cluster's centroid.

In [7]:

from geopy.distance import geodesic

cluster_centroids = clustered_pois.groupby('cluster_id').agg({'lat': 'mean', 'lon': 'mean'})

clustered_pois['distance_to_centroid'] = clustered_pois.apply(
    lambda row: geodesic((row['lat'], row['lon']), (cluster_centroids.loc[row['cluster_id'], 'lat'], cluster_centroids.loc[row['cluster_id'], 'lon'])).km,
    axis=1
)

cluster_summary = clustered_pois.groupby('cluster_id').size().reset_index(name='restaurant_count')
cluster_summary['cluster_color'] = cluster_summary['cluster_id'].map(cluster_colors)
cluster_summary['average_distance_to_centroid'] = clustered_pois.groupby('cluster_id')['distance_to_centroid'].mean().reset_index()['distance_to_centroid']

summary_dict = cluster_summary.set_index('cluster_id').to_dict(orient='index')

summary_dict

{0: {'restaurant_count': 2743,
  'cluster_color': 'blue',
  'average_distance_to_centroid': 2.2633106262235865},
 1: {'restaurant_count': 242,
  'cluster_color': 'red',
  'average_distance_to_centroid': 5.473680588665231},
 2: {'restaurant_count': 464,
  'cluster_color': 'green',
  'average_distance_to_centroid': 8.81096203560978},
 3: {'restaurant_count': 208,
  'cluster_color': 'black',
  'average_distance_to_centroid': 5.548455523125211},
 4: {'restaurant_count': 508,
  'cluster_color': 'purple',
  'average_distance_to_centroid': 4.486509401180799}}

These numbers support what we are seeing on the map. The blue cluster, located in the center of Madrid, has significantly more restaurants than all the others, with 2743 restaurants. Additionally, the average distance of each restaurant to the cluster centroid is less than in the other clusters.

Other clusters, such as the green one, have fewer restaurants, only 464 in this case, but with a higher average distance to the centroid, which is 8.8km.

If we have no other options and can only create 5 zones to group deliveries, these numbers suggest that we can expect a high volume of deliveries from the center of Madrid. Considering the lower average distance to the centroid in this cluster, we can implement a strategy to handle multiple deliveries from different restaurants simultaneously, taking advantage of its higher density despite its smaller geographic extent.

However, this strategy may not be feasible for clusters like the green one, where the average distance to the centroid is 8.8km. In this case, it may be advisable to consider splitting this cluster into two or more separate clusters.

Lets try to see what happens if we increase the number of clusters, for example lets increase it to 8. 

In [9]:
restaurants_with_8_clusters = split_pois_by_clusters(restaurants_far_from_cinemas, 8)

# Define a color palette for different cluster IDs
cluster_colors = {
    0: 'blue',
    1: 'red',
    2: 'green',
    3: 'black',
    4: 'purple',
    5: 'orange',
    6: 'pink',
    7: 'brown'
}

# We use a map centered in Madrid with a zoom level to see all the POIs
madrid_map = folium.Map(location=[40.4168, -3.7038], zoom_start=11)

for index, row in restaurants_with_8_clusters.iterrows():
    cluster_id = row['cluster_id']
    color = cluster_colors.get(cluster_id, 'gray') 
    folium.CircleMarker(
        location=[row['lat'], row['lon']],
        radius=4,
        color=color,
        fill=True,
        fill_color=color
    ).add_to(madrid_map)

madrid_map


/Users/mafer/Downloads/carto-challenge/geo_analytics/processing.py:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['cluster_id'] = kmeans.labels_


Is clear that with a highest number of clusters, we have a better distribution of our delivery zones.

## Extra Balls

The REST API for fetching the cluster given a restaurant_id is implemented, and you can check how to test it in the `README.md` file.

### Equal-sized clusters

The second extra task involves generating k-clusters, each with the same number of elements. This is not an easy problem to solve, and there are many different approaches and algorithms available, none of which are simple; they are complex and challenging to implement.

Initially, I considered the possibility of implementing a Python version of the algorithm used by the ELKI data mining framework. They have an excellent [tutorial](https://elki-project.github.io/tutorial/same-size_k_means) on equal-size k-means. I even found a [Github repository](https://github.com/ndanielsen/Same-Size-K-Means) where someone had the same idea. However, as we can see, the implementation of this algorithm is complex, and given the time constraints of a code challenge, it might be too ambitious.

While exploring different solutions, I came across a [paper](https://www.microsoft.com/en-us/research/wp-content/uploads/2016/02/tr-2000-65.pdf) written by P. S. Bradley at Microsoft. Essentially, they faced a similar problem: they wanted to avoid ending up with clusters that were almost empty or clusters with significantly more elements than others. Of course, this algorithm is even more complex to implement, but there is a [python module](https://github.com/joshlk/k-means-constrained) that implements the same idea.

In [10]:
from k_means_constrained import KMeansConstrained

clf = KMeansConstrained(
    n_clusters=5,
    size_min=len(clustered_pois) // 5,
    size_max=len(clustered_pois) // 5 + 1,
    random_state=0
)

clf.fit(clustered_pois[['lat', 'lon']])

clustered_pois['cluster_id'] = clf.labels_

# Define a color palette for different cluster IDs
cluster_colors = {
    0: 'blue',
    1: 'red',
    2: 'green',
    3: 'black',
    4: 'purple'
}

# We use a map centered in Madrid with a zoom level to see all the POIs
madrid_map = folium.Map(location=[40.4168, -3.7038], zoom_start=11)

for index, row in clustered_pois.iterrows():
    cluster_id = row['cluster_id']
    color = cluster_colors.get(cluster_id, 'gray') 
    folium.CircleMarker(
        location=[row['lat'], row['lon']],
        radius=4,
        color=color,
        fill=True,
        fill_color=color
    ).add_to(madrid_map)

madrid_map



As we can see, a lot of restaurants from the center of Madrid are distributed to the others Clusters using this method. As mentioned on the paper, Equal-sized clusters are useful when you have a lot of dimensions, but in our case we only have two, so probably a typical K-means algorithm would work fine fo our case as we saw before.